In [42]:
import pandas as pd
import numpy as np
import os
from datetime import date
import datetime
import time
from tqdm import tqdm
import yfinance as yf
from sklearn.decomposition import PCA
from sklearn.preprocessing import MinMaxScaler
pd.set_option('display.max_rows', 10000)

# Class for aggregating longitudinally

In [102]:
class CreateLongData:
    """
    """
    def __init__(self, directory, df):
        self.directory = directory
        self.df = df

    def usa_stocks(self, date):
        files = os.listdir(f"{self.directory}/{date}")
        usa_stocks_file = [x for x in files if (x.startswith('usa_stocks')) & (x.endswith('.csv'))][0]
        df = pd.read_csv(f"{self.directory}/{date}/{usa_stocks_file}").iloc[:, 1:]
        # remove % from values
        df = df.replace({'%':''}, regex=True) 
        # no change during after hours
        df['After-Hours Change'] = df['After-Hours Change'].replace(np.nan, 0) 
        # drop fundamentals for now
        df = df.drop(['Company', 'Industry', 'Country', 'P/E', 'Forward P/E', 'P/B', 'Dividend Yield', 'Total Debt/Equity',
                      'EPS growth this year', 'EPS growth next year'], axis=1) 
        # remove stock with missing market cap data
        df = df[~df['Market Cap'].isna()] 
        # remove remaining stock with missing either instituional ownership, float short, short ratio, volatility, rsi
        df = df.dropna() 
        # ensure all columns are numerics
        df = pd.concat([df[['Ticker', 'Sector']], df.drop(['Ticker', 'Sector'], axis=1).apply(pd.to_numeric)], axis=1)
        # convert % to decimals
        perc_cols = ['Dividend Yield','EPS growth this year','EPS growth next year','Institutional Ownership',
                     'Institutional Transactions','Float Short','Performance (Week)','Performance (Month)',
                     'Volatility (Week)','Volatility (Month)','20-Day Simple Moving Average','50-Day Simple Moving Average',
                     '200-Day Simple Moving Average','50-Day High','50-Day Low','52-Week High','52-Week Low',
                     'Relative Strength Index (14)','Change from Open','Gap','Change','After-Hours Change']
        df[list(set(df.columns).intersection(set(perc_cols)))] = df[list(set(df.columns).intersection(set(perc_cols)))]/100
        # clean up column names
        df.columns = df.columns.str.replace("(", "")
        df.columns = df.columns.str.replace(")", "")
        df.columns = df.columns.str.replace("-", "_")
        df.columns = df.columns.str.replace(" ", "_")
        # add date
        df['date'] = datetime.datetime.strptime(date, '%m-%d-%Y')
        return df

    def technical_signals(self, date, df_all):
        files = os.listdir(f"{self.directory}/{date}")
        signal_files = [x for x in files if ((x.startswith('signal')) | (x.startswith('dv'))) & (x.endswith('.csv'))]
        # iterate through all technical indicators
        for i in signal_files:
            # for each stock flagged by the specified technical indicator in the filename, join to main df
            df_signal = pd.read_csv(f"{self.directory}/{date}/{i}").iloc[:, 1:]
            signal_col = i.replace('.csv','')
            # 1 for technical indicator satisfied
            df_signal[signal_col] = 1
            df_all = df_all.merge(df_signal, on='Ticker', how='left')
            # 0 if technical indicator not satisfied
            df_all[signal_col] = df_all[signal_col].replace(np.nan, 0)         
        return df_all
    
    def get_vix(self):
        end = date.today() + datetime.timedelta(days=1)
        start = self.df['date'].min()
        vix = yf.download('^VIX', start=start, end=end)
        vix = vix.reset_index()
        vix_close = vix[['Date', 'Close']].rename(columns={'Close':'vix', 'Date':'date'})
        return vix_close
    
    def create_lag_feats(self, df, num_lags=1):
        # lag all current_ columns
        df_lag = df.copy()
        current_cols = [x for x in df_lag.columns if x.startswith('current')]
        for i in tqdm(range(1, num_lags + 1)):
            for j in current_cols:
                col_name = j.replace('current', f"previous{i}")
                df_lag[col_name] = df_lag.groupby('ticker')[j].shift(i)
        return df_lag
    
    def create_dv(self, df):
        df_dv = df.copy()
        # create dependent variables based off current features
        df_dv['dv_5perc_inc_from_open'] = np.select([df_dv['current_change_from_open'] >= 0.05,
                                                     df_dv['current_change_from_open'] <= 0], [1, 0], np.nan)
        df_dv['dv_2perc_inc_from_open'] = np.select([df_dv['current_change_from_open'] >= 0.02,
                                                     df_dv['current_change_from_open'] <= 0], [1, 0], np.nan)
        df_dv['dv_1perc_inc_from_open'] = np.select([df_dv['current_change_from_open'] >= 0.01,
                                                     df_dv['current_change_from_open'] <= 0], [1, 0], np.nan)
        df_dv['dv_close_up_from_open'] = np.select([df_dv['current_change_from_open'] > 0,
                                                    df_dv['current_change_from_open'] <= 0], [1, 0], np.nan)
        df_dv['dv_top_gainer'] = np.select([(df_dv['current_candlestick_marubozu_white'] == 1) |
                                            (df_dv['current_indicator_top_gainers'] == 1),
                                            df_dv['current_change_from_open'] <= 0], [1, 0], np.nan) 
        df_dv['dv_doji'] = np.where((df_dv['current_candlestick_doji'] == 1) |
                                    (df_dv['current_candlestick_dragon_fly_doji'] == 1) |
                                    (df_dv['current_candlestick_gravestone_doji'] == 1), 1, 0)
        return df_dv
    
    def get_summary(self, df):
        df_sum = df.copy()
        sum_stats = pd.DataFrame(df_sum.describe())
        num_non_zero = pd.DataFrame((df_sum != 0).astype(int).sum()).T
        num_non_zero = num_non_zero.rename(index={0: 'Num_non_zeros'})
        final_sum = pd.concat([sum_stats, num_non_zero], axis=0)[1:]
        final_sum = final_sum.T.reset_index().rename(columns={'index':'Feature'})
        return final_sum
    
    def scale_features(self, df, cols):
        df_scale = df.copy()
        min_max_scaler = MinMaxScaler()
        df_scale[cols] = min_max_scaler.fit_transform(df_scale[cols])
        df_scale = df_scale[cols]
        df_scale.columns = [x.replace('current', 'current_scaled') for x in df_scale.columns]
        return df_scale
    
    def do_pca(self, df, cols, num_comp, names):
        def_pca = PCA(n_components=num_comp)
        pca_out = def_pca.fit_transform(df[cols])
        #sum(def_pca.explained_variance_ratio_)
        cols_for_df = [f"current_{names}{x}" for x in range(1, num_comp + 1)]
        df_pca = pd.DataFrame(data = pca_out, columns = cols_for_df)
        return df_pca
    
    def combine_long(self):
        # first scan directory for new data
        files = os.listdir(f"{self.directory}")
        df_dates = [datetime.datetime.strptime(x, '%Y-%m-%d') for x in self.df['date'].tolist()]
        new_files = [x for x in files if (datetime.datetime.strptime(x, '%m-%d-%Y') not in df_dates) &
                     (datetime.datetime.strptime(x, '%m-%d-%Y') > min(df_dates))]
        if not new_files:
            print("Data is up to date")
        else:
            print(f"Detetected {len(new_files)} new files. Updating now.")
            for i in tqdm(new_files):
                df1 = self.usa_stocks(i)
                df2 = self.technical_signals(i, df1)
                #vix_df = self.get_vix()
                #df2 = df2.merge(vix_df, on='Date', how='left')
                df_updt = pd.concat([self.df, df2], axis=0)
                df_updt['date'] = pd.to_datetime(df_updt['date'])
                df_updt = df_updt[['date', 'Ticker'] + df_updt.drop(['date', 'Ticker'], axis=1).columns.tolist()]
                self.df = df_updt.sort_values(['Ticker', 'date']).reset_index().drop(['index'], axis=1)
            # add in vix
            vix_df = self.get_vix()
            self.df = self.df.merge(vix_df, on='date', how='left')
            # clean-up columns names
            candlesticks = ['signal_doji', 'signal_hammer', 'signal_long_lower_shadow', 'signal_long_upper_shadow',
                            'signal_inverted_hammer', 'signal_spinning_top_white', 'signal_spinning_top_black',
                            'signal_dragon_fly_doji', 'signal_gravestone_doji', 'signal_marubozu_white', 'signal_marubozu_black']
            patterns = ['signal_channel_down', 'signal_channel_up', 'signal_double_bottom', 'signal_double_top',
                        'signal_head_and_shoulders', 'signal_head_and_shoulders_inverse', 'signal_horizontal',
                        'signal_multiple_top', 'signal_multple_bottom', 'signal_triangle_ascending', 'signal_triangle_descending',
                        'signal_tl_resistance', 'signal_tl_support', 'signal_wedge', 'signal_wedge_down', 'signal_wedge_up']
            self.df.columns = [x.replace('signal', 'candlestick') if x in candlesticks else x for x in self.df.columns]
            self.df.columns = [x.replace('signal', 'pattern') if x in patterns else x for x in self.df.columns]
            self.df.columns = self.df.columns.str.replace('signal', 'indicator')
            self.df.columns = self.df.columns.str.replace('dv', 'indicator')
            self.df.columns = ['current_' + x if x not in ['date', 'Ticker', 'Sector'] else x for x in self.df.columns]
            self.df.columns = self.df.columns.str.lower()
            # add in day of week
            self.df['current_day_of_week'] = self.df['date'].dt.dayofweek
            # scale features
            feats_to_scale = ['current_market_cap', 'current_institutional_ownership', 'current_institutional_transactions',
                              'current_float_short', 'current_short_ratio', 'current_performance_week',
                              'current_performance_month', 'current_average_true_range', 'current_volatility_week',
                              'current_volatility_month', 'current_20_day_simple_moving_average',
                              'current_50_day_simple_moving_average', 'current_200_day_simple_moving_average',
                              'current_50_day_high', 'current_50_day_low', 'current_52_week_high', 'current_52_week_low',
                              'current_relative_strength_index_14', 'current_change_from_open', 'current_gap',
                              'current_average_volume', 'current_relative_volume', 'current_price', 'current_change',
                              'current_after_hours_change', 'current_vix', 'current_day_of_week']
            df_scaled = self.scale_features(self.df, feats_to_scale)
            self.df = pd.concat([self.df, df_scaled], axis=1)
            # replace all missing with nan
            self.df = self.df.fillna(0)
            # do pca
            cont_cols = [x for x in self.df.columns if x.startswith('current_scaled')]
            pci_cols = [x for x in self.df.columns if (('pattern' in x) | ('candle' in x) |
                                                       ('indicator' in x)) & (x.startswith('current'))]
            pca_df_cont = self.do_pca(self.df, cont_cols, 5, 'pca_cont')
            pca_df_pci = self.do_pca(self.df, pci_cols, 25, 'pca_pci')
            self.df = pd.concat([self.df, pca_df_cont, pca_df_pci], axis=1)
            # add in lag terms
            self.df = self.create_lag_feats(self.df, num_lags=1)
            # add dv variables
            self.df = self.create_dv(self.df)
            # write out data
            self.df.to_csv('df_long.csv', index=False)
        return self.df
    

In [103]:
df_init = pd.DataFrame()
init_date = '10-01-2021'

# initialize class
cld = CreateLongData(directory='D:/Finviz Data', df=df_init)
df_init = cld.usa_stocks(date=init_date)
df_init = cld.technical_signals(date=init_date, df_all=df_init)
df_init.to_csv('df_long.csv', index=False)
df_init

Ticker                  Sector  Market_Cap  Institutional_Ownership  \
0          A              Healthcare    47687.70                   0.9030   
1         AA         Basic Materials     9145.24                   0.7900   
2        AAC               Financial     1217.46                   0.5870   
3       AADI              Healthcare      611.03                   0.1090   
4       AAIC             Real Estate      119.61                   0.4410   
5        AAL             Industrials    13285.74                   0.5470   
6       AAMC               Financial       45.81                   0.2690   
7       AAME               Financial       84.71                   0.0650   
8        AAN             Industrials      899.76                   0.9400   
9       AAOI              Technology      194.92                   0.4910   
10      AAON             Industrials     3424.42                   0.7200   
11      AAPL              Technology  2339019.11                   0.5880   
12       AAT             Real Estate     2263.06                   0.9820   
13      AATC              Technology       39.57                   0.2870   
14        AB               Financial     4948.47                   0.1410   
15      ABBV              Healthcare   190624.95                   0.6870   
16       ABC              Healthcare    24819.84                   0.6600   
17      ABCB               Financial     3619.53                   0.9140   
18      ABEO              Healthcare      113.40                   0.2830   
19      ABGI               Financial      188.28                   0.8710   
20      ABIO              Healthcare       42.71                   0.0830   
21       ABM             Industrials     3026.40                   0.9530   
22      ABMD              Healthcare    14772.95                   0.9360   
23      ABNB  Communication Services   105454.78                   0.4780   
24       ABR             Real Estate     2634.13                   0.4570   
25       ABT              Healthcare   209422.62                   0.7530   
26      ABTX               Financial      771.06                   0.5180   
27      ABUS              Healthcare      425.39                   0.3180   
28        AC               Financial      826.77                   0.7200   
29      ACAD              Healthcare     2668.32                   0.9440   
30      ACBI               Financial      537.70                   0.8670   
31       ACC             Real Estate     6739.69                   0.9470   
32      ACCD              Healthcare     2786.38                   0.6890   
33      ACCO             Industrials      821.07                   0.9040   
34      ACEL       Consumer Cyclical     1139.30                   0.6540   
35      ACER              Healthcare       36.61                   0.2970   
36      ACET              Healthcare      249.59                   0.6690   
37      ACEV               Financial      284.91                   0.4190   
38       ACI      Consumer Defensive    14523.29                   0.5950   
39      ACII               Financial      420.91                   0.6010   
40      ACIW              Technology     3610.35                   0.9940   
41      ACLS              Technology     1579.16                   0.8800   
42       ACM             Industrials     9097.56                   0.8820   
43      ACMR              Technology     2132.60                   0.4870   
44      ACNB               Financial      244.17                   0.2120   
45      ACOR              Healthcare       51.18                   0.3470   
46      ACQR               Financial      383.96                   0.8230   
47       ACR             Real Estate      152.45                   0.4480   
48      ACRE             Real Estate      708.86                   0.5210   
49      ACRS              Healthcare     1101.90                   0.9520   
50      ACRX              Healthcare      121.60                   0.2540   
51

In [104]:
cld = CreateLongData(directory='D:/Finviz Data', df=pd.read_csv('df_long.csv'))
df_long = cld.combine_long()
df_long

  0%|                                                                                                                                                                                                               | 0/6 [00:00<?, ?it/s]

Detetected 6 new files. Updating now.


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:04<00:00,  1.26it/s]

[*********************100%***********************]  1 of 1 completed

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:03<00:00,  3.34s/it]


date ticker      sector  current_market_cap  \
0     2021-10-01      A  Healthcare            47687.70   
1     2021-10-04      A  Healthcare            46577.98   
2     2021-10-05      A  Healthcare            46782.80   
3     2021-10-06      A  Healthcare            46972.34   
4     2021-10-07      A  Healthcare            47482.88   
...          ...    ...         ...                 ...   
25345 2021-10-05   ZYXI  Healthcare              392.67   
25346 2021-10-06   ZYXI  Healthcare              394.80   
25347 2021-10-07   ZYXI  Healthcare              399.43   
25348 2021-10-08   ZYXI  Healthcare              397.30   
25349 2021-10-11   ZYXI  Healthcare              390.39   

       current_institutional_ownership  current_institutional_transactions  \
0                                0.903                              0.0100   
1                                0.903                              0.0100   
2                                0.903                              0.0100   
3                                0.903                              0.0100   
4                                0.903                              0.0100   
...                                ...                                 ...   
25345                            0.318                             -0.0374   
25346                            0.318                             -0.0374   
25347                            0.318                             -0.0374   
25348                            0.318                             -0.0374   
25349                            0.316                             -0.0003   

       current_float_short  current_short_ratio  current_performance_week  \
0                   0.0114                 2.07                   -0.0952   
1                   0.0114                 2.07                   -0.0843   
2                   0.0114                 2.06                   -0.0430   
3                   0.0114                 2.06                   -0.0397   
4                   0.0114                 2.07                   -0.0140   
...                    ...                  ...                       ...   
25345               0.1841                11.39                   -0.0645   
25346               0.1841                11.44                   -0.0423   
25347               0.1841                11.49                   -0.0149   
25348               0.1841                11.57                    0.0036   
25349               0.1841                11.63                    0.0314   

       current_performance_month  ...  previous1_pca_pci22  \
0                        -0.1109  ...                  NaN   
1                        -0.1441  ...            -0.046065   
2                        -0.1464  ...            -0.041944   
3                        -0.1354  ...            -0.035490   
4                        -0.1310  ...            -0.024055   
...                          ...  ...                  ...   
25345                    -0.1631  ...            -0.049006   
25346                    -0.1547  ...            -0.016993   
25347                    -0.1302  ...            -0.016993   
25348                    -0.1261  ...            -0.048052   
25349                    -0.1142  ...            -0.020529   

       previous1_pca_pci23  previous1_pca_pci24  previous1_pca_pci25  \
0                      NaN                  NaN                  NaN   
1                -0.073942             0.157339             0.025709   
2                 0.011672            -0.038851            -0.022064   
3                -0.020897             0.025157             0.011055   
4                 0.037875            -0.058781            -0.039120   
...                    ...                  ...                  ...   
25345             0.029178            -0.049678             0.000644   
25346             0.020370            -0.047955            -0.061827   
25347             0.020370            -0.047955 

In [105]:
cld.get_summary(df_long)

Feature          mean  \
0                                   current_market_cap  1.267511e+04   
1                      current_institutional_ownership  6.381418e-01   
2                   current_institutional_transactions  9.486683e-02   
3                                  current_float_short  4.344321e-02   
4                                  current_short_ratio  4.587475e+00   
5                             current_performance_week -6.419207e-03   
6                            current_performance_month -2.004314e-02   
7                           current_average_true_range  3.072218e+00   
8                              current_volatility_week  3.933278e-02   
9                             current_volatility_month  3.903253e-02   
10                current_20_day_simple_moving_average -7.074966e-03   
11                current_50_day_simple_moving_average -9.791030e-03   
12               current_200_day_simple_moving_average -1.394147e-02   
13                                 current_50_day_high -1.358268e-01   
14                                  current_50_day_low  1.448805e-01   
15                                current_52_week_high -2.733450e-01   
16                                 current_52_week_low  8.613796e-01   
17                  current_relative_strength_index_14  4.913637e-01   
18                            current_change_from_open -8.340237e-04   
19                                         current_gap  1.040000e-03   
20                              current_average_volume  1.333373e+03   
21                             current_relative_volume  1.103503e+00   
22                                       current_price  1.588711e+02   
23                                      current_change  1.819250e-04   
24                          current_after_hours_change  9.063984e-04   
25                        current_pattern_channel_down  1.072978e-02   
26                          current_pattern_channel_up  9.980276e-03   
27                            current_candlestick_doji  2.729783e-02   
28                       current_pattern_double_bottom  1.112426e-02   
29                          current_pattern_double_top  9.822485e-03   
30                        current_indicator_downgrades  3.274162e-03   
31                   current_indicator_earnings_before  3.550296e-04   
32                          current_candlestick_hammer  3.388560e-02   
33                  current_pattern_head_and_shoulders  6.351085e-03   
34          current_pattern_head_and_shoulders_inverse  3.550296e-04   
35                  current_indicator_high_short_float  2.023669e-02   
36                          current_pattern_horizontal  1.100592e-02   
37                current_indicator_lt_3perc_above_low  2.536489e-01   
38               current_indicator_lt_3perc_below_high  2.422485e-01   
39                        current_indicator_major_news  7.928994e-03   
40                       current_indicator_most_active  2.773176e-02   
41                     current_indicator_most_volatile  2.666667e-02   
42                        current_pattern_multiple_top  5.917160e-03   
43                      current_pattern_multple_bottom  1.234714e-02   
44                          current_indicator_new_high  3.151874e-02   
45                           current_indicator_new_low  1.956607e-02   
46                        current_indicator_overbought  4.181460e-03   
47                          current_indicator_oversold  3.076923e-03   
48              current_indicator_price_above_20daysma  4.742801e-01   
49      current_indicator_price_crossed_above_20daysma  1.081262e-01   
50             current_indicator_recent_insider_buying  1.881657e-02   
51            current_indicator_recent_insider_selling  2.268245e-02   
52              current_indicator_relative_volume_gt_5  9.940828e-03   
53                       current_pattern_tl_resistance  8.284024e-03   
54                          current_pattern_tl_support  9.467456e-03   
55             

In [3]:
# Additional feature ideas
    
# Modeling pipeline
    # RNN
    # Mixed effect logistic regression
    # Use output of above models as features for an xgboost with hyperparameter tuning for final prediction
    
# performance tracking
    
# Dependent variable ideas

